In [19]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
import time
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.chrome.service import Service as ChromeService
from selenium.webdriver.support.ui import WebDriverWait, Select
from selenium.webdriver.support import expected_conditions as EC
# import undetected_chromedriver as uc

In [41]:
scrape_category = ["cleanser", "face-mask", "sunscreen-sun-protection", 
                   "moisturizing-cream-oils-mists", "facial-treatments", 
                   "lip-balm-lip-care", "eye-treatment-dark-circle-treatment"]
# ex_url = "https://www.sephora.com/shop/sunscreen-sun-protection"

# options = uc.ChromeOptions() #subject to change
# prefs = {"download.default_directory" : "/Users/bowiechuang/Downloads/"} # download file directory path location
# options.add_argument("--disable-gpu")
# options.add_argument("--disable-blink-features=AutomationControlled")
# options.add_experimental_option("prefs", prefs)
# service = ChromeService("/Users/bowiechuang/Downloads/chromedriver-mac-arm64/chromedriver") # path of chromedriver location
# driver = uc.Chrome(options = options) # set up driver

# def scroll_down(driver, n_scroll):
#     body = driver.find_element_by_the_tag_name("body")
#     while n_scroll >= 0:
#         body.send_keys(Keys.PAGE_DOWN)
#         nscroll -= 1
#     return driver

# try:
#     driver.get(ex_url)
#     wait = WebDriverWait(driver, 10)
#     # browser = scroll_down(driver, 5)
    
#     # time.sleep(5)

#     content = driver.page_source # retrive html content
#     soup = BeautifulSoup(content, 'html.parser')

# except:
#     print("unsuccessful")
# finally:
#     print("Scrape Complete")
#     driver.close()


Scrape Complete


In [53]:
import requests
from bs4 import BeautifulSoup
import pandas as pd

# Step 1: Extract all product URLs from the sitemap
sitemap_url = "https://www.sephora.com/sitemaps/products-sitemap_en-CA.xml"

from selenium import webdriver
import time

# Initialize Selenium WebDriver
options = webdriver.ChromeOptions()
options.add_argument("--disable-gpu")
driver = webdriver.Chrome(options = options)  # Ensure you have ChromeDriver installed
driver.get(sitemap_url)

time.sleep(5)

# Get the page source after fully loading
sitemap_html = driver.page_source

driver.quit()

In [54]:
print(soup.prettify())

<urlset xmlns="http://www.sitemaps.org/schemas/sitemap/0.9" xmlns:xhtml="http://www.w3.org/1999/xhtml">
 <url>
  <loc>
   https://www.sephora.com/ca/en/product/one-size-by-patrick-starrr-turn-up-base-buttersilk-concealer-P473741
  </loc>
  <changefreq>
   daily
  </changefreq>
  <priority>
   0.5
  </priority>
  <xhtml:link href="https://www.sephora.com/ca/en/product/one-size-by-patrick-starrr-turn-up-base-buttersilk-concealer-P473741" hreflang="x-default" rel="alternate">
  </xhtml:link>
  <xhtml:link href="https://www.sephora.com/product/one-size-by-patrick-starrr-turn-up-base-buttersilk-concealer-P473741" hreflang="en-US" rel="alternate">
  </xhtml:link>
  <xhtml:link href="https://www.sephora.com/ca/en/product/one-size-by-patrick-starrr-turn-up-base-buttersilk-concealer-P473741" hreflang="en-CA" rel="alternate">
  </xhtml:link>
  <xhtml:link href="https://www.sephora.com/ca/fr/product/one-size-by-patrick-starrr-turn-up-base-buttersilk-concealer-P473741" hreflang="fr-CA" rel="altern

##### Data to scrape: Type of product, name, review, brand, number of reviews, price, size, skin type, skincare concern, What it is

In [6]:
# Base URL for Sephora's skincare - Cleansers category
baseurl = "https://www.sephora.com/shop/cleanser?currentPage={}"

In [7]:
# Base URL for Sephora's skincare - Masks category
baseurl_masks = "https://www.sephora.com/shop/face-mask?currentPage={}"

In [8]:
# Base URL for Sephora's skincare - Sunscreen category
baseurl_sunscreen = "https://www.sephora.com/shop/sunscreen-sun-protection?currentPage={}"

In [9]:
# Base URL for Sephora's skincare - Moisturizer category
baseurl_moisturizers = "https://www.sephora.com/shop/moisturizing-cream-oils-mists?currentPage={}"

In [11]:
# Base URL for Sephora's skincare - Treatments category
baseurl_treatments = "https://www.sephora.com/shop/facial-treatments?currentPage={}"

In [12]:
# Base URL for Sephora's skincare - Lip Balms & Treatments category
baseurl_lips = "https://www.sephora.com/shop/lip-balm-lip-care?currentPage={}"

In [ ]:
# Base URL for Sephora's skincare - Eye Care category
baseurl_eyecare = "https://www.sephora.com/shop/eye-treatment-dark-circle-treatment?currentPage={}"

# IGNORE EVERYTHING ON TOP

In [1]:
import pandas as pd
import numpy as np
from bs4 import BeautifulSoup
from selenium import webdriver
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.common.by import By  # Import By 
from selenium.webdriver.common.keys import Keys  # Import Keys for scrolling
import requests
import time
import re

categorized_df = pd.read_excel("/Users/bowiechuang/Documents/GitHub/Skin_Care_Recommendation/sephora_product_list.xlsx")
#Testing
test_links = categorized_df['link'][401:405]

def scrollDown(driver, n_scroll):
    elem = driver.find_element(By.TAG_NAME, "html")
    while n_scroll >= 0:
        elem.send_keys(Keys.PAGE_DOWN)
        n_scroll -= 1
    return driver

# Setup Chrome options
options = Options()
options.add_argument("--disable-gpu")

options.add_argument("user-agent=Mozilla/5.0 (Macintosh; arm64; Mac OS X 14_3) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/120.0.0.0 Safari/537.36")
# options.add_argument("user-agent=Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/114.0.5735.90 Safari/537.36") #Christina's agent 
options.add_argument("--disable-blink-features=AutomationControlled")

# Initialize the WebDriver
driver = webdriver.Chrome(options=options)  # Ensure ChromeDriver is installed and in PATH

# Loop through each link in categorized_df['link']
products_list = []
for link in test_links:
    try:
        driver.get(link)
        time.sleep(10)  # Give page time to load
        
        #Check link if the page redirects to "productnotcarried"
        if "/search?" in driver.current_url:
          print(f" Skipping unavailable product: {link}")
          continue
        
        while True:
            browser = scrollDown(driver, 20) #scroll down the page
            time.sleep(10) #give it time to load
            break
        
        #Parse Page Source
        soup = BeautifulSoup(driver.page_source, 'html.parser')
        
        # Extract product name
        prod_name_element = soup.find('span', {'data-at': 'product_name'})  # Use find instead of find_all

        if prod_name_element:
          prod_name = prod_name_element.text.strip()  # Extract text
          prod_name = " ".join(word for word in prod_name.split() if word.lower() != "hair")  # Remove "Hair" from product           name
        else:
          prod_name = "N/A"  # Default value if not found

         # Extract brand name
        prod_element = soup.find('a', class_=['css-1kj9pbo e15t7owz0', 'css-wkag1e e15t7owz0'])
        brand_name = prod_element.text.strip() if prod_element else "N/A"
        
        # Removed 'size' from string. 
        #Extract brand size
        size = soup.find(['span', 'div'], class_ = ['css-15ro776', 'css-1wc0aja e15t7owz0'])
        if size:
          prod_size = size.text.strip()   # Extract text 
          prod_size = prod_size.replace('Size:', '').replace('Size', '').strip()  # Remove "Size" and extra details
        else:
          prod_size = "N/A"  # Default if not found
          
        #Product type
        category = categorized_df.loc[categorized_df['link'] == link, 'category'].values
        category = category[0] if len(category) > 0 else "N/A"  
        
        #Extract product price
        price = soup.find('b', class_='css-0')
        prod_price = price.text.strip() if price else "N/A"
        
        #Extract product rating class="css-egw4ri e15t7owz0" 
        #rating = soup.find_all("span", attrs={"class": "css-egw4ri e15t7owz0"})
        rating = soup.find_all("span", class_=re.compile(".*css-egw4ri.*e15t7owz0.*"))

        # Ensure there's at least one match before accessing index 0
        if rating:
          prod_rating = rating[0].text.strip()  # Get first match
        else:
          prod_rating = "N/A"  # Default value if no match found
        
        #Extract brand reviews
        review = soup.find_all('span', class_ = 'css-1dae9ku e15t7owz0')
        if review:
          prod_reviews = review[0].text.strip()  # Get full text
          match = re.search(r'\d+', prod_reviews)  # Extract only the first number
          prod_reviews = match.group(0) if match else "N/A"  # Get the matched number

        #Extract Description
        # Locate all divs that may contain product descriptions
        description_classes = soup.find_all('div', class_=['css-1v2oqzv e15t7owz0', 'css-1j9v5fd e15t7owz0', 'css-1uzy5bx e15t7owz0'])

        description_tags = ['p', 'b', 'strong']

        # Initialize default value
        prod_desc = "N/A"

        element_desc = []
        for class_name in description_classes:
          element_desc.extend(soup.find_all('div', class_=class_name))

        for div in element_desc:
          for tag in description_tags:
            element = div.find(tag)
            # Check if the element contains "What it is:"
            if element and "What it is:" in element.text:
            # Extract text while handling possible formatting issues
              extracted_text = element.get_text(separator=" ", strip=True).replace("What it is:", "").strip()

            # Case 2: The description follows the tag as a sibling text
              if not extracted_text and element.next_sibling:
                extracted_text = element.next_sibling.strip()

            # Case 3: Handle cases where the text is split across multiple <br> tags
              if not extracted_text:
                extracted_text = []
                next_element = element.find_next_sibling(text=True)
                while next_element:
                  extracted_text.append(next_element.strip())
                  next_element = next_element.find_next_sibling(text=True)
                extracted_text = " ".join(extracted_text).strip()

          # If valid text is found, set it and stop searching
              if extracted_text:
                prod_desc = extracted_text
                break # Stop searching once we find a valid description

          if prod_desc != "N/A":
            break  # Stop checking other divs once we get the correct description

        # Print the extracted product description
        print(f"Product Description: {prod_desc}")


        #Extract Skin Types
        element_types = soup.find_all('div', class_ = ['css-1v2oqzv e15t7owz0', 'css-1j9v5fd e15t7owz0', 'css-1uzy5bx e15t7owz0'])

        skin_type = "N/A"

        for div in element_types:
          strong_elements = div.find_all(['strong', 'b'])  # Find all <strong> and <b> elements in this div

          for tag in strong_elements:
            if "Skin Type:" in tag.text:
              next_text = tag.next_sibling
              if next_text and next_text.strip():
                skin_type = next_text.strip()
              else:
                next_container = tag.find_next_sibling()  # Backup check for next sibling
                if next_container:
                  skin_type = next_container.get_text(strip=True)

        #Extract Concerns
        element_concerns = soup.find_all('div', class_ = ['css-1v2oqzv e15t7owz0', 'css-1j9v5fd e15t7owz0', 'css-1uzy5bx e15t7owz0'])

        # Initialize default values
        skin_concerns = "N/A"

        for div in element_concerns:
          strong_elements = div.find_all(['strong','b'])  # Find all <strong> elements in this div

          for tag in strong_elements:
            if "Skincare Concerns:" in tag.text:
              next_text = tag.next_sibling  # Get text after <b> or <strong>
              if next_text and next_text.strip():
                skin_concerns = next_text.strip().replace("-", "")
              else:
                next_container = tag.find_next_sibling()  # Backup check for next sibling
                if next_container:
                  skin_concerns = next_container.get_text(strip=True).replace("-", "")


          # Handle cases where concerns are listed inside separate `<p>` tags
          p_tags = div.find_all('p')
          p_concerns = [p.text.strip().replace("-", "").strip() for p in p_tags if p.text.strip()]
          # If `<p>` contains concerns, update values
          if p_concerns:
            if "Skincare Concerns:" in strong_elements:
              skin_concerns = ", ".join(p_concerns)  # Join multiple concerns
              
        #Extract Ingredients
        ingredient_element = soup.find('div', class_ = 'css-1mb29v0 e15t7owz0')
        if ingredient_element:
          prod_ingredients = ingredient_element.text.strip()
        else:
          prod_ingredients = 'N/A'
  
        # Append data
        products_list.append({"Brand Name": brand_name,
                              "Product Name": prod_name,
                              "Product Category": category,
                              "Product Price": prod_price,
                              "Product Rating": prod_rating,
                              "Product Size": prod_size,
                              "Product Reviews": prod_reviews,
                              "Product Description": prod_desc,
                              "Product Ingredients": prod_ingredients,
                              "Skin Type": skin_type,
                              "Skin Concerns": skin_concerns,
                              "URL": link})
        #check if it processes link 
        print(f" processed: {link}")

    except Exception as e:
        print(f" Error processing {link}: {e}")

# Close WebDriver *after* processing all links
driver.quit()

product_df = pd.DataFrame(products_list)
print(product_df)





 Error processing https://www.sephora.com/ca/en/product/innbeauty-project-slushy-serum-moisturizer-crush-infused-with-bakuchiol-P471037: argument of type 'NoneType' is not iterable
 Error processing https://www.sephora.com/ca/en/product/the-inkey-list-pha-exfoliating-hydrating-body-water-cream-P511110: Message: no such window: target window already closed
from unknown error: web view not found
  (Session info: chrome=133.0.6943.142)
Stacktrace:
0   chromedriver                        0x00000001028942d4 cxxbridge1$str$ptr + 2739836
1   chromedriver                        0x000000010288c934 cxxbridge1$str$ptr + 2708700
2   chromedriver                        0x00000001023edf90 cxxbridge1$string$len + 93360
3   chromedriver                        0x00000001023c7964 chromedriver + 129380
4   chromedriver                        0x000000010245cedc cxxbridge1$string$len + 547836
5   chromedriver                        0x0000000102475994 cxxbridge1$string$len + 648884
6   chromedriver         

KeyboardInterrupt: 